In [9]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import pickle

In [10]:
# read csv file
reader_df = pd.read_csv('../dataset/validate_data_with_bert.csv')

In [11]:
reader_df

Id                                              Title  Price  \
0      0826414346                           dr. seuss: american icon    NaN   
1      0826414346                           dr. seuss: american icon    NaN   
2      0963923080  rising sons and daughters: life among japan's ...    NaN   
3      0854968350  muslim women's choices: religious belief and s...    NaN   
4      157067051X  voices from the farm: adventures in community ...    NaN   
...           ...                                                ...    ...   
86131  0425200736                         echoes (berkley sensation)    NaN   
86132  0786182431                   very bad deaths: library edition   90.0   
86133  0786182431                   very bad deaths: library edition   90.0   
86134  0786182431                   very bad deaths: library edition   90.0   
86135  B000NSLVCU                                the idea of history    NaN   

              User_id                    profileName review/helpfulness  \
0      A30TK6U7DNS82R                  Kevin Killian              10/10   
1      A14OJS0VWMOSWO            Midwest Book Review                3/4   
2      A3NIQK6ZLYEP1L            Michael Valdivielso                0/0   
3       ATDE9JYCPI0L1               Alyssa A. Lappen                0/0   
4      A1ER5AYS3FQ9O3             K. Corn "reviewer"                6/7   
...               ...                            ...                ...   
86131     AFVQZQ8PW0L               Harriet Klausner                4/5   
86132  A2CR57GAJKNWVV  booksforabuck "BooksForABuck"                6/8   
86133  A1I2O9Y3X3HXLS               Arthur W. Jordin                1/1   
86134     AFVQZQ8PW0L               Harriet Klausner                5/7   
86135  A1SMUB9ASL5L9Y                        jafrank                1/1   

       review/score  review/time  \
0               5.0   1095724800   
1               5.0   1100131200   
2               4.0   1239667200   
3               2.0   1109808000   
4               5.0   1160870400   
...             ...          ...   
86131           5.0   1099180800   
86132           4.0   1106956800   
86133           5.0   1230595200   
86134           5.0   1103846400   
86135           4.0   1331683200   

                                          review/summary  \
0                                      Really Enjoyed It   
1      A memorably excellent survey of Dr. Seuss' man...   
2                               Almost a day by day view   
3                                                Oh dear   
4      Intense memoir told in brief segments by forme...   
...                                                  ...   
86131                         Engaging romantic suspense   
86132                            Thoughtful and Powerful   
86133                            The Perils of Telepathy   
86134            fantastic paranormal serial killer tale   
86135      Quite good and ahead of its time occasionally   

                                             review/text  \
0      I don't care much for Dr. Seuss but after read...   
1      Theodor Seuss Giesel was best known as 'Dr. Se...   
2      Steven Wardell went to Japan without reading a...   
3      I was excited to find a book ostensibly about ...   
4      This book gave me a glimpse at life on The Far...   
...                                                  ...   
86131  Mountain Bend, California elementary school pr...   
86132  Russell Walker wants to be left alone to die--...   
86133  Very Bad Deaths (2004) is the first SF novel i...   
86134  Fiftyish Canadian Russell Walker writes "The F...   
86135  This is pretty interesting. Collingwood seems ...   

                                             description  \
0      Philip Nel takes a fascinating look into the k...   
1      Philip Nel takes a fascinating look into the k...   
2      Wardell recalls his experience as a foreign st...   
3      Counters the Western views and stereotypes 

In [12]:
reader_df = reader_df.drop(['Price', 'profileName', 'review/summary', 'review/text', \
                                                      'description', 'authors', 'publisher'], axis = 1)
# get year from publishedDate
reader_df['publishedDate'] = reader_df['publishedDate'].str.split('-').str[0]
# fill the missing value with the most frequent year
reader_df['publishedDate'] = reader_df['publishedDate'].fillna(reader_df['publishedDate'].value_counts().index[0])
# handle the year with ?, replace with the most frequent year of that century (19xx)
reader_df.loc[reader_df['publishedDate'].str.find("?") != -1, 'publishedDate'] = reader_df.loc[reader_df['publishedDate'].str[:2] == '19', 'publishedDate'].value_counts().index[0]
# remove the * sign in the publishedDate
reader_df['publishedDate'] = reader_df['publishedDate'].str.replace('*', '')
reader_df['publishedDate'] = reader_df['publishedDate'].astype(int)

# one-hot encoding for book category
reader_df['categories'] = reader_df['categories'].str.replace('[', '').str.replace(']', '').str.replace("'", '')
# build category list
category_list = reader_df['categories'].unique().tolist()
reader_df = pd.get_dummies(reader_df, columns=['categories'])

# helpfulness ratio
reader_df['review/helpfulness'] = reader_df['review/helpfulness'].str.split('/').str[0].astype(float) / reader_df['review/helpfulness'].str.split('/').str[1].astype(float)
reader_df['review/helpfulness'] = reader_df['review/helpfulness'].fillna(0)

In [13]:
reader_id_list = reader_df['User_id'].unique().tolist()
train_reader_buying_list = {}
for reader in reader_id_list:
    train_reader_buying_list[reader] = [[], []]
    tmp_df = reader_df[reader_df['User_id'] == reader]
    train_reader_buying_list[reader][0] = tmp_df.sort_values(by=['review/score'], ascending=False)['Id'].tolist()
    train_reader_buying_list[reader][1] = tmp_df.sort_values(by=['review/score'], ascending=False)['review/score'].tolist()

In [14]:
reader_id_list = reader_df['User_id'].unique().tolist()
reader_buying_list = {}
attribute_dict = {
    'User_id': [],
    'avg_helpfulness': [],
    'start_buying_year': [],
    'end_buying_year': [],
}
for category in category_list:
    attribute_dict["ratio_" + category] = []
    attribute_dict["score_" + category] = []
for reader in reader_id_list:
    attribute_dict['User_id'].append(reader)
    tmp_df = reader_df[reader_df['User_id'] == reader]
    attribute_dict['avg_helpfulness'].append(tmp_df['review/helpfulness'].mean())
    attribute_dict['start_buying_year'].append(tmp_df['publishedDate'].min())
    attribute_dict['end_buying_year'].append(tmp_df['publishedDate'].max())
    reader_buying_list[reader] = [[], []]
    reader_buying_list[reader][0] = tmp_df.sort_values(by=['review/score'], ascending=False)['Title'].tolist()
    reader_buying_list[reader][1] = tmp_df.sort_values(by=['review/score'], ascending=False)['review/score'].tolist()
    for category in category_list:
        # ratio of buying books in each category
        attribute_dict["ratio_" + category].append(tmp_df['categories_' + category].sum() / tmp_df.shape[0])
        # average review score of buying books in each category
        score_mean = tmp_df[tmp_df['categories_' + category] == 1]['review/score'].mean()
        attribute_dict["score_" + category].append(0 if np.isnan(score_mean) else score_mean)

reader_df = pd.DataFrame(attribute_dict)
# normalize the data
reader_df['avg_helpfulness'] = (reader_df['avg_helpfulness'] - reader_df['avg_helpfulness'].min()) / (reader_df['avg_helpfulness'].max() - reader_df['avg_helpfulness'].min())
reader_df['start_buying_year'] = (reader_df['start_buying_year'] - reader_df['start_buying_year'].min()) / (reader_df['start_buying_year'].max() - reader_df['start_buying_year'].min())
reader_df['end_buying_year'] = (reader_df['end_buying_year'] - reader_df['end_buying_year'].min()) / (reader_df['end_buying_year'].max() - reader_df['end_buying_year'].min())
for category in category_list:
    reader_df["ratio_" + category] = (reader_df["ratio_" + category] - reader_df["ratio_" + category].min()) / (reader_df["ratio_" + category].max() - reader_df["ratio_" + category].min())
    reader_df["score_" + category] = (reader_df["score_" + category] - reader_df["score_" + category].min()) / (reader_df["score_" + category].max() - reader_df["score_" + category].min())

In [15]:
reader_df

User_id  avg_helpfulness  start_buying_year  end_buying_year  \
0    A30TK6U7DNS82R         0.716382           0.958969         0.857143   
1    A14OJS0VWMOSWO         0.700399           0.937401         0.857143   
2    A3NIQK6ZLYEP1L         0.618646           0.937401         0.857143   
3     ATDE9JYCPI0L1         0.815510           0.984745         0.714286   
4    A1ER5AYS3FQ9O3         0.841288           0.991583         0.857143   
..              ...              ...                ...              ...   
813  A3TZV5SXQ8F6ST         0.628550           0.993161         0.857143   
814  A1LI7KZH6VHPAQ         0.849318           0.985797         0.714286   
815   A76FRFSYRN1TK         0.786917           0.991583         0.857143   
816  A29E0Q47E8CPPO         0.592595           0.973172         0.714286   
817  A3LEH416AV3VTU         0.372150           0.972120         0.857143   

     ratio_Biography & Autobiography  score_Biography & Autobiography  \
0                           0.484559                         0.847273   
1                           0.196595                         1.000000   
2                           0.083965                         0.980000   
3                           0.160161                         0.933333   
4                           0.436210                         0.930000   
..                               ...                              ...   
813                         0.412722                         0.900000   
814                         0.000000                         0.000000   
815                         0.156883                         0.720000   
816                         0.121252                         0.900000   
817                         0.080080                         0.733333   

     ratio_Social Science  score_Social Science  ratio_Religion  \
0                0.023091              0.666667        0.010930   
1                0.075100              1.000000        0.106148   
2                0.051350              0.942857        0.005208   
3                0.093284              0.750000        0.215252   
4                0.057165              0.800000        0.000000   
..                    ...                   ...             ...   
813              0.060096              1.000000        0.021334   
814              0.000000              0.000000        0.000000   
815              0.000000              0.000000        0.038925   
816              0.000000              0.000000        0.000000   
817              0.000000              0.000000        0.000000   

     score_Religion  ...  ratio_Fiction  score_Fiction  \
0          0.800000  ...       0.527094       0.854206   
1          1.000000  ...       0.226079       0.999606   
2          1.000000  ...       0.690141       0.888435   
3          0.769231  ...       0.089552       1.000000   
4          0.000000  ...       0.439024       0.894444   
..              ...  ...            ...            ...   
813        1.000000  ...       0.384615       0.760000   
814        0.000000  ...       0.019231       1.000000   
815        0.900000  ...       0.736842       0.880952   
816        0.000000  ...       0.525424       0.793548   
817        0.000000  ...       0.895522       0.806667   

     ratio_Business & Economics  score_Business & Economics  ratio_Computers  \
0                      0.005445                    1.000000         0.010310   
1                      0.108214                    0.999091         0.057751   
2                      0.005189                    0.600000         0.000000   
3                      0.032993                    1.000000         0.000000   
4                      0.053915                    0.850000         0.000000   
..                          ...                         ...              ...   
813                    0.021255                    1.000000         0.000000   
814                    0.000000                    0.000000         0.000000   


In [16]:
reader_buying_list

{'A30TK6U7DNS82R': [['dr. seuss: american icon',
   'not without love: memoirs',
   'the l shaped room',
   'tilt-a-whirl',
   'dear people: remembering jonestown',
   'the hollow (winterbrook edition)',
   'secret anniversaries of the heart: new and selected stories by lev raphael',
   'finnegans wake',
   "a summer of faulkner: as i lay dying/the sound and the fury/light in august (oprah's book club)",
   'spark notes our town',
   'ultimate gay erotica 2005',
   'fiddlers',
   'you can say you knew me when',
   'swing: a mystery',
   'wodehouse: a life',
   'ariel',
   'a day, a night, another day, summer: stories',
   'the oracle: the lost secrets and hidden messages of ancient delphi',
   'doctor zhivago',
   'my life',
   'fiddlers (87th precinct mysteries)',
   'funny accent: a novel',
   'sgt. york: his life, legend & legacy: the remarkable untold story of sgt. alvin c. york',
   'murder in mesopotamia: a hercule poirot mystery',
   'a star over bethlehem and other stories',
  

In [17]:
with open('../dataset/reader_buying_list.pkl', 'wb') as f:
    pickle.dump(reader_buying_list, f)

In [8]:
# reader_df.to_csv('../dataset/reader_info.csv', index=False)